In [1]:
from PIL import Image
import numpy as np
from tqdm import tqdm_notebook as tqdm

from bokeh.plotting import figure
from bokeh.io import push_notebook, show, output_notebook
from bokeh.models import ColumnDataSource
from bokeh.models.widgets import Div
from bokeh.layouts import row, column
from bokeh.palettes import Colorblind
from  ipywidgets import interact
output_notebook()

from recaps.utils import euler_forward, runge_kutta2, get_dynamic_plots

Loading BokehJS ...

Loading BokehJS ...

### Building intuition on simple systems

In general, the reaction-diffusion pdes, that we saw in the previous section, can equally well describe homogeneous systems that oscillate in time (systems with Hopf bifurcation), inhomogenous steady systems (systems with Turing bifurcation), as well as inhomogenous oscillating systems. So what regulates the behaviour and determines the patterns? Well, the ability to accomodate various patterns depends on complexity of the reaction term, but the exact nature of patterns depends on system parameters. 

So, if we select the reactions and set the parameters, we can simulate the system and check how it behaves. That's exactly what we did in the previous section. But can we _predict_ this behaviour _without_ simulation? Just from looking at the parameters? And, more importantly, if we're interested in a very particular behaviour, is there a way to pick the corresponding parameters without checking each and every combination, untill we finally hit the right one? The answer is "_sort of_": we can't determine which parameters in Gray-Scott system will lead to the formation of ["U-skates"](http://mrob.com/pub/comp/xmorphia/uskate-world.html), but we can map the regions with more general types of bifurcation in parameter space. Doing this would require us to remember some bits and pieces of the Linear Algebra. But before we start remembering, let's just play around with the simpler systems and try to build up some intuition first.

### Simple homogeneous oscillators

Let's forget about the diffusion for a moment, and pretend that we have a homogeneous system. Suppose that we have an activator-inhibitor system of two genes: $A$ inhibits $B$ and $B$ activates $A$. To keep things simple let's assume linear relation between the expression _rates_ ($\frac{dc_{A}}{dt}$ and $\frac{dc_{B}}{dt}$) and expression _levels_ ($c_{A}$ and $c_{B}$):

<img width="300" height="50" src="images/ode_simple_oscillator.png"></img>

Let's check how the system would behave if we vary parameters $k_{AB}$ and $k_{BA}$. We'll start with the function, which reflects the mass balances of the two species.


In [5]:
# ---define the system---
# mass balance: all we know about the system is stored here
def balances(_, x, p):
    """dc_a/dt =  k_ba*c_b
       dc_b/dt = -k_ab*c_a"""     
    x_a, x_b = x[0], x[1]
   
    return np.array([ p['k_ba'] * x_b,  # dc_a/dt
                      p['k_ab'] * x_a]) # dc_b/dt

This function only calculates the rates of changes in $A$ and $B$ over a single time step. So, to find how the expression levels of $A$ and $B$ change over long periods of time, we'll need to repeat the same calculation for different time steps. This time we'll use second order [Runge Kutta](https://en.wikipedia.org/wiki/Runge%E2%80%93Kutta_methods) method.

><font size=2>Quick recap: [numerical solutions of ordinary differential equations](recaps/numerical_solutions_recap.ipynb)</font>

In [10]:
# ---set up solver (Runge Kutta 2)---
def runge_kutta2(dxdt, x, t_span, p):
    x = x.astype(float)
    
    # preallocate/initialize
    x_span = np.zeros((len(x), len(t_span)))
    x_span[:,0] = x
        
    for it,t in enumerate(t_span[1:]):
        dt = t_span[it+1] - t_span[it]
        k1 = dxdt(t,        x,        p)*dt
        k2 = dxdt(t+0.5*dt, x+0.5*k1, p)*dt
        x += k2
        x_span[:,it+1] = x
        
    return x_span 

#---specify some useful stuff---
# time related
t0,dt,tf = 0,0.001,50
t_span = np.arange(t0,tf+dt,dt)

# initial condition
x0 = np.array([0.5,  # c_a(t=0)
               0.5]) # c_b(t=0)

# parameters
p = {'k_ba':  0.5,
     'k_ab': -0.5}
        
# ---simulate the system---
x_num = runge_kutta2(balances, x0, t_span, p)

In [12]:
# ---plot stuff!---
title = "simple homogeneous oscillator"
labels = ["time", "expression level"]
legend = ["expression level of A", "expression level of B"]
comment = "<br>Perhaps assuming linear relation\
           between expression rates and expression levels\
           wasn't a great idea - <br>\
           now our system has genes with negative expression... fantastic...<br><br>\
           We can fix it by assuming more realistic nonlinear kinetics, \
           but let's not do it just yet. \
           After all, we're only trying to build intuition\
           while playing with simple maths here."

def get_dynamic_plots(t_span, x_num, title, labels, legend, comment=""):
    # plot states as functions of time
    y_min, y_max = min(x_num.ravel()), max(x_num.ravel()) 
    plt1 = figure(title=title, 
                  x_range=[t_span[0], t_span[-1]], 
                  y_range=[y_min - 0.3*(y_max-y_min), y_max + 0.3*(y_max-y_min)],
                  plot_width=450, plot_height=250)
    plt1.xaxis.axis_label = labels[0]
    plt1.yaxis.axis_label = labels[1]
    
    colors = Colorblind[max(len(x_num), min(Colorblind.keys()))]
    r1 = [plt1.line(t_span, x_num[i,:], color=colors[i], line_width=2, legend=legend[i])
          for i in range(len(x_num))]
    
    # plot x2 as a functino of x1
    x_min, x_max, y_min, y_max = min(x_num[0,:]), max(x_num[0,:]), min(x_num[1,:]), max(x_num[1,:])
    plt2 = figure(x_range=[x_min - 0.3*(x_max-x_min), x_max + 0.3*(x_max-x_min)],
                  y_range=[y_min - 0.3*(y_max-y_min), y_max + 0.3*(y_max-y_min)],
                  plot_width=250, plot_height=250)
    plt2.xaxis.axis_label = legend[0]
    plt2.yaxis.axis_label = legend[1]
    r2 = plt2.line(x_num[0,:], x_num[1,:], color=colors[0], line_width=2)

    div = Div(width=250, text=comment)

    show(row(plt1, plt2, div), notebook_handle=True)    
    return plt1, plt2, r1, r2

plt1, plt2, r1, r2 = get_dynamic_plots(t_span, x_num, title, labels, legend, comment=comment)   


# add interactive sliders to check the effect of parameters and dt
def update(p_ab=0.25, p_ba=-0.25, dt=0.05):
    t = np.arange(t0,tf+dt,dt)
    c_a, c_b = runge_kutta2(balances, x0, t, {'k_ba': p_ba, 'k_ab': p_ab})
    
    r1[0].data_source.data = {'x': t,   'y': c_a}
    r1[1].data_source.data = {'x': t,   'y': c_b}
    r2.data_source.data  = {'x': c_a, 'y': c_b}
    push_notebook()

interact(update, p_ab=(-1,1,0.005), p_ba=(-1,1,0.005), dt=(0.05,2,0.05))


interactive(children=(FloatSlider(value=0.25, description='p_ab', max=1.0, min=-1.0, step=0.005), FloatSlider(value=-0.25, description='p_ba', max=1.0, min=-1.0, step=0.005), FloatSlider(value=0.05, description='dt', max=2.0, min=0.05, step=0.05), Output()), _dom_classes=('widget-interact',))

<function __main__.update>

This system happens to oscillate, whenever two parameters ($k_{AB}$ and $k_{BA}$) have opposite signs (when one gene acts as activator and the other - as inhibitor). And when two parameters have the same signs (so we have either two activators or two inhibitors) the system "explodes"... That's not particularly interesting... So  let's make a small correction: suppose expression of $A$ can now be self-inhibited by its level is too high:

<img width="400" height="50" src="images/ode_simple_oscillator_with_inhibition.png"></img>

In [20]:
def balances(_, x, p):
    """dc_a/dt = -k_aa*c_a + k_ba*c_b
       dc_b/dt = -k_ab*c_a           """ 
    c_a, c_b = x[0], x[1]
    
    return np.array([p['k_aa']*c_a + p['k_ba']*c_b,
                     p['k_ab']*c_a])

p = {'k_aa': -0.10,
     'k_ba':  0.25,
     'k_ab': -0.25}

# ---simulate---
x_num = runge_kutta2(balances, x0, t_span, p)

# ---plot stuff!---
show(row(plt1, plt2), notebook_handle=True)

# add interactive sliders to check the effect of parameters and dt
def update(p_aa=-0.10, p_ab=0.25, p_ba=-0.25, dt=0.05):
    t = np.arange(t0,tf+dt,dt)
    c_a, c_b = runge_kutta2(balances, x0, t, {'k_aa':p_aa, 'k_ba':p_ba, 'k_ab':p_ab})
    
    r1[0].data_source.data = {'x': t,   'y': c_a}
    r1[1].data_source.data = {'x': t,   'y': c_b}
    r2.data_source.data  = {'x': c_a, 'y': c_b}
    push_notebook()

interact(update, p_aa=(-1,1,0.005), p_ab=(-1,1,0.005), p_ba=(-1,1,0.005), dt=(0.05,2,0.05))
    

interactive(children=(FloatSlider(value=-0.1, description='p_aa', max=1.0, min=-1.0, step=0.005), FloatSlider(value=0.25, description='p_ab', max=1.0, min=-1.0, step=0.005), FloatSlider(value=-0.25, description='p_ba', max=1.0, min=-1.0, step=0.005), FloatSlider(value=0.05, description='dt', max=2.0, min=0.05, step=0.05), Output()), _dom_classes=('widget-interact',))

<function __main__.update>

By introducing self-inhibition ($k_{AA} c_A$ term) we got ourselves a damper! Now we can regulate whether or when the system reaches stable steady state. 

One thing we can still check, is the effect of self-activation/inhibition of $B$. By now you can probably figure out yourself, what needs to be changed in the code, to account for this process. So just go ahead - modify the code above and check how it affects system's behaviour.

### What does Linear Algebra have to do with any of this

Toggling the parameters is fun, but it's definitely not the most systematic way of analyzing the system. We can do better. Luckily, since our system is linear, we can unleash all the tools that Linear Algebra has to offer (and that's a lot)! To see what we can do, let's first rewrite the system in a more Linear-Algebra-compliant (and somewhat cleaner) form:

$$ \begin{cases} \frac{dx_{A}}{dt} = -k_{AA}x_{A} + k_{BA}x_{B} \\
                 \frac{dx_{B}}{dt} = -k_{AB}x_{A} \end{cases} \rightarrow
   \begin{cases} \frac{dx_{A}}{dt} = -k_{AA}x_{A} + k_{BA}x_{B} \\
                 \frac{dx_{B}}{dt} = -k_{AB}x_{A} + 0\cdot x_{B} \end{cases} \rightarrow
   \begin{bmatrix} \frac{dx_{A}}{dt} \\ \frac{dx_{B}}{dt} \end{bmatrix} = 
   \begin{bmatrix} -k_{AA} & k_{BA} \\ -k_{AB} & 0 \end{bmatrix} \cdot 
   \begin{bmatrix} x_{A} \\ x_{B} \end{bmatrix} \rightarrow 
   \dot{\textbf{x}} = \textbf{A} \textbf{x} $$
   
where $\dot{\textbf{x}} = \begin{bmatrix} \frac{dx_{A}}{dt} \\ \frac{dx_{B}}{dt} \end{bmatrix}$, 
      $\textbf{x} = \begin{bmatrix} x_{A} \\ x_{B} \end{bmatrix}$ and
      $\textbf{A} = \begin{bmatrix} -k_{AA} & k_{BA} \\ -k_{AB} & 0 \end{bmatrix}$.
      
><font size=2>
 The $\textbf{A}$ matrix (not to be confused with gene $A$) is called the _state matrix_, because it transforms the _state vector_ $\textbf{x}$. But you could've also recognized it as [Jacobian](https://en.wikipedia.org/wiki/Jacobian_matrix_and_determinant), as it is composed of first order partial derivatives of system ode's with respect to each of the states. </font>

Just like solution of linear ode would have a form $x = const\cdot e^{\lambda t}$, a solution of _system_ of linear ode's without intput terms would have a form $\textbf{x} = \textbf{v}e^{\lambda t}$ (now both $\textbf{x}$ and $\textbf{v}$ are vectors). The main question is, how do we find $\textbf{v}$ and $\lambda$... Let's plug in this generic candidate solution into the system definition:

$$ \dot{\textbf{x}} = \textbf{A} \textbf{x} \rightarrow 
   \lambda \textbf{v} e^{\lambda t} = \textbf{A} \textbf{v}e^{\lambda t} \rightarrow 
   \lambda \textbf{v} = \textbf{A} \textbf{v} $$
   
Did you recognize the last expression? It says that transforming the unknown vector $\textbf{v}$ by a matrix $\textbf{A}$ is equivalent to just scaling this vector by some constant coefficient $\lambda$ in all directions. Well, isn't it a textbook definition of [eigenvectors](https://en.wikipedia.org/wiki/Eigenvalues_and_eigenvectors)! For us this means that $\textbf{x} = \textbf{v}e^{\lambda t}$ can only be a solution of $\dot{\textbf{x}} = \textbf{A} \textbf{x}$ if $\textbf{v}$ is the eigenvector of $\textbf{A}$ and $\lambda$ is the corresponding eigenvalue.      
      

In [14]:
A = np.array([[-0.10, 0.25],
              [-0.25, 0   ]])
eigval, eigvec = np.linalg.eig(A)

print('\neigenvalues: \n{}'.format(eigval))
print('\neigenvectors: \n{}'.format(eigvec))


eigenvalues: 
[-0.05+0.24494897j -0.05-0.24494897j]

eigenvectors: 
[[0.70710678+0.j         0.70710678-0.j        ]
 [0.14142136+0.69282032j 0.14142136-0.69282032j]]


Oh, for 2x2 matrix there are two eigenvalues and two eigenvectors... Which ones do we choose? Well, both. Since our system is linear, the [linear combination](https://en.wikipedia.org/wiki/Linear_combination) (weighted sum) of its solutions would also be a solution. So the general solution would look something like: 

$$ \textbf{x} = \alpha \textbf{v}_{1}e^{\lambda_1 t} + \beta \textbf{v}_{2}e^{\lambda_2 t}$$ 

where $\alpha$ and $\beta$ are some coefficients, that can be found as long as we know the state $\textbf{x}$ of the system at $t=0$:

$$ \textbf{x}_0 = \alpha \textbf{v}_{1}e^{\lambda_1 \cdot 0} + \beta \textbf{v}_{2}e^{\lambda_2 \cdot 0} = \
   \alpha\textbf{v}_1 + \beta \textbf{v}_2 = \
   \begin{bmatrix} \textbf{v}_1 & \textbf{v}_2 \end{bmatrix} \cdot \begin{bmatrix} \alpha \\ \beta \end{bmatrix}$$

In [15]:
coef = np.linalg.solve(eigvec, x0)
print('coefficients: \n{} \n{}'.format(coef[0], coef[1]))

coefficients: 
(0.35355339059327384-0.28867513459481287j) 
(0.35355339059327384+0.28867513459481287j)


In [16]:
# confirm if these coefficients indeed solve x0 = eigvec.coef
np.allclose(np.dot(eigvec, coef), x0)

True

By the way, did you notice that the calculated eigenvalues are complex? What does it mean for the ode solution? Remember that the solution for each state $x$ would have a general form $\text{constant} \cdot e^{\lambda t}$. If lambda is complex, we can write:

<center><br>
$ x = 
  \text{const} \cdot e^{\lambda t} = 
  \text{const} \cdot exp\big($ <font color="teal">$Re(\lambda t)$</font> + <font color="indianred">$i\text{ }Im(\lambda t)$    </font> $\big) = \
  \text{const} \cdot $ <font color="teal">$e ^{Re(\lambda t)}$</font> <font color="indianred">$e^{i \text{ } Im(\lambda t)} $</font> 
  $ = \text{const} \cdot$ 
  <font color="teal">$ e^{Re(\lambda t)}$</font>
  <font color="indianred">$\big(cos(Im(\lambda t)) + i\text{ } sin(Im(\lambda t))\big)$</font></center>

><font size=2>Here we used [Euler's formula](https://en.wikipedia.org/wiki/Euler%27s_formula):</font>
><img width="250" height="400" src="images\complex_numbers.png"></img>

It appears that the <font color="indianred">imaginary</font> part of the eigenvalue $\lambda$ is responsible for all the oscillations (if $Im(\lambda t)$ is 0, the whole <font color="indianred">reddish</font> part reduces to $1$ and all the sines and cosines disappear)! And the <font color="teal">real</font> part of $\lambda$ is responsible for modulating the amplitude of these oscillations: if $Re(\lambda t)$ is positive, then the amplitude of the oscillations increases with time and the system "explodes"; and if $Re(\lambda t)$ is negative, the oscillations gradually dampen, and the system converges to stable steady-state. (Can you see what would happen if $Re(\lambda t) = 0$?) 

For us this means, that just by varying the parameters and checking the eigenvalues of the resulting $\textbf{A}$-matrix, we can map system behaviour in parameter space without running any simulations!


In [21]:
p_aa_span, p_ba_span = np.linspace(-1,1,201), np.linspace(-1,1,201)
values   = [[None for _ in range(len(p_ba_span))] for _ in range(len(p_aa_span))]
patterns = [[None for _ in range(len(p_ba_span))] for _ in range(len(p_aa_span))]

# check the eigenvalues for each combination of p_aa and p_ba in given ranges
for ip_aa,p_aa in enumerate(p_aa_span):
    for ip_ba,p_ba in enumerate(p_ba_span):
        A[0,0] = p_aa
        A[0,1] = p_ba
    
        eigval,_ = np.linalg.eig(A)
        
        # yes oscillations
        if np.imag(eigval[0]) or np.imag(eigval[1]): 
            # exploding (undamped)
            if np.real(eigval[0]) > 0 or np.real(eigval[1]) > 0: 
                values[ip_aa][ip_ba] = 0.75
                patterns[ip_aa][ip_ba] = "'exploding' oscillations"
            # periodic -> Hopf bifurcation(critically damped)
            elif np.real(eigval[0]) == 0 and np.real(eigval[1]) == 0:
                values[ip_aa][ip_ba] = 0.5
                patterns[ip_aa][ip_ba] = "periodic oscillations"
            # decaying (subcritically damped -> stable steady-state)
            else:             
                values[ip_aa][ip_ba] = 0.25
                patterns[ip_aa][ip_ba] = "decaying oscillations"
        # no oscillations
        else:
            # exploding
            if eigval[0] > 0 or eigval[1] > 0:
                values[ip_aa][ip_ba] = 1
                patterns[ip_aa][ip_ba] = "'exploding'"
            # stable steady-state
            else:
                values[ip_aa][ip_ba] = 0
                patterns[ip_aa][ip_ba] = "decaying"

data = dict(image=[values],
            pattern=[patterns])

# ---plot stuff!---
# get pattern map
plt3 = figure(x_range=(p_ba_span[0], p_ba_span[-1]),
              y_range=(p_aa_span[0], p_aa_span[-1]),
              plot_width=250, plot_height=250,
              tooltips=[("p_aa", "$y"), ("p_ba", "$x"), ("pattern", "@pattern")],
              title="mouse over the regions")

plt3.image(source=data, image='image', x=-1, y=-1, dw=2, dh=2, palette="Greys256")
plt3.xaxis.axis_label = "p_ba"
plt3.yaxis.axis_label = "p_aa"

# show dynamic plot and pattern map
div = Div(width=210,
          text="""<br>Simulate the system (use sliders) to confirm that the patterns, \
                  mapped by analyzing the eigenvlues, were identified correctly.""")
show(row(plt1, plt3, div), notebook_handle=True)

# add interactive sliders to check the effect of parameters and dt
def update(p_aa=-0.10, p_ba=0.25):
    t = np.arange(0, tf+0.05, 0.05)
    c_a, c_b = runge_kutta2(balances, x0, t, {'k_aa':p_aa, 'k_ba':p_ba, 'k_ab':-0.25})
    
    r1[0].data_source.data = {'x': t,   'y': c_a}
    r1[1].data_source.data = {'x': t,   'y': c_b}
    push_notebook()

interact(update, p_aa=(-1,1,0.005), p_ba=(-1,1,0.005))              

interactive(children=(FloatSlider(value=-0.1, description='p_aa', max=1.0, min=-1.0, step=0.005), FloatSlider(value=0.25, description='p_ba', max=1.0, min=-1.0, step=0.005), Output()), _dom_classes=('widget-interact',))

<function __main__.update>

### How do we extend this for nonlinear systems?

Eigenvalues told us a lot about the patterns in system behaviour... Sorry, eigenvalues told us a lot about the patterns in __linear__ system behaviour (various steps of our analysis relied on the assumption, that we're dealing with linear system). Well, that's a bit meh, since, if we're looking for "interesting" patterns, we should probably look into complex nonlinear systems. Is there _any_ way we can apply what we've learned about the eigenvalues to map the behaviour of nonlinear systems?

Turns out there is a way! And it involves __linearization__ of the nonlinear system. Linearization doesn't mean that we magically replace the nonlinear system with its linear analog without any loss of information. The system can only be linearized __locally__: just like any complex curve can be approximated by a straight line _in a proximity of some point_ if we zoom-in close enought, - any system of nonlinear ode's can also be approximated by a system of linear ode's _in a proximity of some point_. Which point? A decent choice is "some point in time veeery far from now", because often we're only interested in knowing how the system would behave "in the end": will it explode or will it stabilize? Formally "in the end" can mean "at the steady state", which is the same as "when all the changes cease" or $\frac{d\textbf{x}}{dt} = 0$. 

To make it sound less abstract, let's work out an example. Let's look at the classical predator-prey system, that the undergrads are introduced to during their Calculus class. We can assume that we have a closed (no inputs, no outputs) homogeneous system, where rabbits grow on some mysterious unlimited food source at a rate proportional to their population density $\mu_{R} x_{R}$ (where $\mu_R$ is the growth rate of rabbits), and foxes gradually die out at a rate proportional to their population density $b_{F} x_{F}$ (where $b_F$ is the decay rate of foxes)... unless they come across some rabbits. When fox encounter a rabbit, some fraction of rabbit's mass ($Y$) is converted into fox's mass. The rate of fox-rabbit encounters should be proportional to probability of both species being at the same time at the same place: $\mu_{F}x_{F}x_{R}$ (where $\mu_F$ is the growth rate of foxes on rabbits). If we choose that the population density of foxes increases with the same rate $\mu_{F}x_{F}x_{R}$, then the population density of rabbits should decrease at a higher rate $\frac{\mu_{F}}{Y}x_{F}x_{R}$. Then we can write:

<img width="750" height="70" src="images/ode_fox_bun.png"></img>

><font size=2>Does this look like autocatalytic chemical reaction? It definitely looks like autocatalitic chemical reaction.</font>

What would be the population densities of foxes and rabbits at the steady state ($x^{*}_{F}$ and $x^{*}_{R}$)? 

$$ \begin{cases} \frac{dx_R}{dt} = 0 \\ \frac{dx_F}{dt} = 0 \end{cases} \rightarrow 
   \begin{cases} \mu_R x^{*}_R - \frac{\mu_F}{Y} x^{*}_Rx^{*}_F = 0 \\ 
                 \mu_F x^{*}_Rx^{*}_F - b_F x^{*}_F = 0 \end{cases} $$
   
With some high-school algebra we can find $x^{*}_R = \frac{b_F}{\mu_F} $ and $x^{*}_F =  \frac{\mu_R Y}{\mu_F} $ (alternatively, we can be a bit lazy and [estimate $x^{*}_R$ and $x^{*}_F$ numerically](recaps/newton_method.ipynb) using, e.g., [Newton's method](https://en.wikipedia.org/wiki/Newton%27s_method)). Great! Now what...


To carry out the same kind of analysis that we've done for the linear system, we need to rewrite our new system in the form $\dot{\textbf{x}} = \textbf{A} \textbf{x}$. Let's recall that $\textbf{A}$-matrix is a [Jacobian](https://en.wikipedia.org/wiki/Jacobian_matrix_and_determinant), so we can still find it for nonlinear system: 

$$ \begin{bmatrix} \frac{dx_R}{dt} \\ \frac{dx_F}{dt} \end{bmatrix} = 
   \begin{bmatrix} \frac{\partial(\mu_R x_R - \frac{\mu_F}{Y} x_R x_F)}{\partial{x_R}} & 
                   \frac{\partial(\mu_R x_R - \frac{\mu_F}{Y} x_R x_F)}{\partial{x_F}} \\ 
                   \frac{\partial(\mu_F x_R x_F - b_F x_F)}{\partial{x_R}} & 
                   \frac{\partial(\mu_F x_R x_F - b_F x_F)}{\partial{x_F}} \end{bmatrix} \cdot 
   \begin{bmatrix} x_R \\ x_F \end{bmatrix} \rightarrow 
   \begin{bmatrix} \frac{dx_R}{dt} \\ \frac{dx_F}{dt} \end{bmatrix} = 
   \begin{bmatrix} \mu_R - \frac{\mu_F}{Y} x_F & -\frac{\mu_F}{Y} x_R \\
                   \mu_F x_F & \mu_F x_R - b_F \end{bmatrix} \cdot 
   \begin{bmatrix} x_R \\ x_F \end{bmatrix} \rightarrow
   \dot{\textbf{x}} = \textbf{A} \textbf{x} $$ 
   
where $\textbf{A} = \begin{bmatrix} \mu_R - \frac{\mu_F}{Y} x_F & -\frac{\mu_F}{Y} x_R \\ \mu_F x_F & \mu_F x_R - b_F \end{bmatrix}$ varies with time, as states $x_R$ and $x_F$ vary with time. Luckily we've already decided, that we're only interested in system behaviour at the steady state, where $\textbf{A}$-matrix becomes 
$ \textbf{A}^{*} = \begin{bmatrix} \mu_R - \frac{\mu_F}{Y} x^{*}_F & -\frac{\mu_F}{Y} x^{*}_R \\ 
                                   \mu_F x^{*}_F & \mu_F x^{*}_R - b_F \end{bmatrix}$.
                                   
The rest is straightforward: we plug in $x^{*}_R = \frac{b_F}{\mu_F} $ and $x^{*}_F =  \frac{\mu_R Y}{\mu_F} $, calculate eigenvalues of $\textbf{A}^{*}$ and find out, that... no matter which _physically justifiable_ parameter values we choose, the system will _always_ bifurcate (prove it)! Let's confirm it with simulations and move on.


In [12]:
def balances_pred_prey(_, x, p):
    rabbits, foxes = x[0], x[1]
    return np.array([p['mu_r']*rabbits - p['mu_f']/p['y']*rabbits*foxes,
                     p['mu_f']*rabbits*foxes - p['b']*foxes])

# time related
t0,dt,tf = 0,0.001,50
t_span = np.arange(t0,tf+dt,dt)

# initial conditions
x0 = np.array([1., # prey0
               1.])# pred0
# parameters
p = {'mu_r': 0.8, # growth rate of prey
     'mu_f': 0.2, # success rate of predator
     'y'   : 0.5, # predator yield on prey 
     'b'   : 0.5} # decay rate of predator


#---simulate---
x_num = runge_kutta2(balances_pred_prey, x0, t_span, p)

# ---plot stuff!---
title = "predator-prey system"
labels = ["time", "population density"]
legend = ["rabbits", "foxes"]
plt1, plt2, r1, r2 = get_dynamic_plots(t_span, x_num, title, labels, legend)

def update(mu_r=0.8, mu_f=0.2, y=0.5, b=0.5):
    t = np.arange(0, tf+0.05, 0.05)
    rabbits, foxes = runge_kutta2(balances_pred_prey, x0, t, {'mu_r':mu_r, 'mu_f':mu_f, 'y':y, 'b':b})
    
    r1[0].data_source.data = {'x': t,      'y': rabbits}
    r1[1].data_source.data = {'x': t,      'y': foxes}
    r2.data_source.data    = {'x': rabbits,'y': foxes}
    push_notebook()

interact(update, mu_r=(0,1,0.005), mu_f=(0,1,0.005), y=(0,1,0.05), b=(0,1,0.05)) 

interactive(children=(FloatSlider(value=0.8, description='mu_r', max=1.0, step=0.005), FloatSlider(value=0.2, description='mu_f', max=1.0, step=0.005), FloatSlider(value=0.5, description='y', max=1.0, step=0.05), FloatSlider(value=0.5, description='b', max=1.0, step=0.05), Output()), _dom_classes=('widget-interact',))

<function __main__.update>

### What would happen if we add diffusion?

We already know, that if we can rewrite the system of some nonlinear ode's $\dot{\textbf{x}} = f(\textbf{x}, p)$ in the linearized form $\dot{\textbf{x}} = \textbf{A}^*\textbf{x}$, then the eigenvalues of $\textbf{A}^*$-matrix can tell us how the system will behave at some point in time, around which it was linearized. 

Can we apply the same thinking to the systems with diffusion $\dot{\textbf{x}} = D\nabla^2 \textbf{x} + f(\textbf{x}, p)$? Absolutely! The idea is the same: we need to rewrite the system $\dot{\textbf{x}} = D\nabla^2 \textbf{x} + f(\textbf{x}, p)$ in the form $\tilde{\dot{\textbf{x}}} = \tilde{\textbf{A}}\tilde{\textbf{x}}$ ($\tilde{\textbf{x}}$ can be some kind of transforms of the original $\textbf{x}$) and check the eigenvalues of the resulting $\tilde{\textbf{A}}$-matrix! Let's see how we can do it for the predator-prey system from the previous example:

$$ \begin{cases} 
   \frac{dx_R}{dt} = D_R\nabla^2 x_R + \mu_R x_R - \frac{\mu_F}{Y} x_R x_F \\ 
   \frac{dx_F}{dt} = D_F\nabla^2 x_F + \mu_F x_R x_F - b_F x_F 
   \end{cases} \rightarrow \
   \begin{bmatrix}\frac{dx_R}{dt} \\ \frac{dx_F}{dt} \end{bmatrix} = \
   \begin{bmatrix} D_R & 0 \\ 0 & D_F \end{bmatrix} \cdot \
   \begin{bmatrix} \nabla^2 x_R \\ \nabla^2 x_F \end{bmatrix} + \
   \begin{bmatrix} \mu_R - \frac{\mu_F}{Y} x_F & -\frac{\mu_F}{Y} x_R \\
                   k x_{pred} & k x_{prey} - b \end{bmatrix} \cdot 
   \begin{bmatrix} x_R \\ x_F \end{bmatrix}$$ 
   
Err... ok... So how exactly do we deal with $\begin{bmatrix} \nabla^2 x_R \\ \nabla^2 x_F \end{bmatrix}$?

The trick that we need to use here involves remembering that $x_R$ and $x_F$ are just functions, and, as any other functions, they can be represented as weighted sums of sine-waves with set frequencies:

$$ x = \int_{-\infty}^{\infty} \tilde{x}_{\omega}\big(cos(\omega t) + i \text{ }sin(\omega t)\big)d\omega =  \
       \int_{-\infty}^{\infty} \tilde{x}_{\omega} e^{i \text{ } \omega t}d\omega \rightarrow
       \int_{-\infty}^{\infty} \tilde{x}_{k} e^{i \text{ } k r}dk$$
       
where $k$ are the wavenumbers, which we choose ourselves ($k = \frac{\omega t}{r}$ - total radians per unit of distance $r$), and $\tilde{x}_{k}$ are the weights (amplitudes) of corresponding wavenumbers. 

To approximate the original $x$'s _perfectly_, we'd need infinitely many sine-waves, with frequencies ranging from $-\infty$ to $+\infty$. But in practice, to approximate $x$ _well_, high but finite number of frequencies will suffice. That's exactly the idea behind [Fourier decomposition](https://en.wikipedia.org/wiki/Fourier_series).

It might not be very clear, how Fourier can help us linearize the system. If anything, it seems to be obfuscating things even more... Even though it might seem this way, we're, in fact, finally about to simlify things: the integral will help us to cancel out the derivatives in $\begin{bmatrix} \nabla^2 x_R \\ \nabla^2 x_F \end{bmatrix}$! 

If we plug $\int_{-\infty}^{\infty} \tilde{x}_{k} e^{i \text{ } k r}dk $ in our system definition, then with some determination we can get:

$$ \begin{cases} 
   \frac{d\tilde{x}_{R,k}}{dt} = -k^2D_R\tilde{x}_{R,k} + \mu_R \tilde{x}_{R,k} - \frac{\mu_F}{Y} \tilde{x}_{R,k}\tilde{x}_{F,k} \\ 
   \frac{d\tilde{x}_{F,k}}{dt} = -k^2D_F\tilde{x}_{F,k} + \mu_F \tilde{x}_{R,k}\tilde{x}_{F,k} - b_F \tilde{x}_{F,k} 
   \end{cases} \rightarrow $$
   
$$ \begin{bmatrix}\frac{d\tilde{x}_{R,k}}{dt} \\ \frac{d\tilde{x}_{F,k}}{dt} \end{bmatrix} = \
   \begin{bmatrix} \mu_R - \frac{\mu_F}{Y} \tilde{x}_{F,k} -k^2D_R & -\frac{\mu_F}{Y} \tilde{x}_{R,k} \\
                   \mu_F \tilde{x}_{F,k} & \mu_F \tilde{x}_{R,k} - b_F -k^2D_F \end{bmatrix} \cdot 
   \begin{bmatrix} \tilde{x}_{R,k} \\ \tilde{x}_{F,k} \end{bmatrix} \rightarrow $$ 
   
$$ \tilde{\dot{\textbf{x}}} = \tilde{\textbf{A}}\tilde{\textbf{x}}$$

where $\tilde{\textbf{A}} = \
       \begin{bmatrix} \mu_R - \frac{\mu_F}{Y} \tilde{x}_{F,k} -k^2D_R & -\frac{\mu_F}{Y} \tilde{x}_{F,k} \\
                       \mu_F \tilde{x}_{F,k} & \mu_F \tilde{x}_{R,k} - b_F -k^2D_F \end{bmatrix} $.

Fantastic! That's exactly what we need. Now guess what would happen if we choose such parameters, that the resulting eigenvalues of $\tilde{\textbf{A}}$ would be imaginary? Yup, the system will oscillate... in space. This means that foxes and rabbits would aggregage in some locations forming spatial patterns. Will these patterns change with time or will they stabilize? To answer that we can just check the eigenvalues of $ \textbf{A}^{*} = \begin{bmatrix} \mu_R - \frac{\mu_F}{Y} x^{*}_F & -\frac{\mu_F}{Y} x^{*}_R \\ \mu_F x^{*}_F & \mu_F x^{*}_R - b_F \end{bmatrix}$ (the one that we've found in the previous section - before considering any diffusion)! If these eigenvalues would have negative real part, we'll eventually have stable dots or stripes or whatnot; and if these eigenvalues would have only imaginary part - we'll have forever changing "spatial waves"! 

